In [9]:
%%writefile project1_s_1.c
#include <stdio.h>
#include <stdlib.h>
#include <pthread.h>
#include <semaphore.h>
#include <unistd.h>
#include <time.h>

// 4 semaphores: 2 for small array max function and 2 for large array max function
// No empty semaphore as shared value does not need to be empty to be overwritten
sem_t mutex1, data1, mutex2, data2;
int globalMaxSmall[1] = {0};
int globalMaxLarge[1] = {0};

#define SMALL 32
#define LARGE 131072
int smallArr[SMALL];
int largeArr[LARGE];

// Find maximum in small array by iterating through entire array and comparing to global maximum
// Only write to max when current value is larger than global max
// Semaphores as buffer solution (CMPSC 472 Lecture 6)
void* findMaxSmall(void* arg) {
    for (int i = 0; i < SMALL; i++) {
      if (smallArr[i] > globalMaxSmall[0]) {
        sem_wait(&mutex1); // Get exclusive access to the buffer
        globalMaxSmall[0] = smallArr[i]; // Add item to the buffer

        sem_post(&mutex1); // Release the mutex
        sem_post(&data1); // Notify that a slot is filled
      }
    }
    pthread_exit(NULL);
  }


// Find maximum in large array by iterating through entire array and comparing to global maximum
// Only write to max when current value is larger than global max
// Semaphores as buffer solution (CMPSC 472 Lecture 6)
void* findMaxLarge(void* arg) {
    for (int i = 0; i < LARGE; i++) {
      if (largeArr[i] > globalMaxLarge[0]) {
        sem_wait(&mutex2); // Get exclusive access to the buffer
        globalMaxLarge[0] = largeArr[i]; // Add item to the buffer

        sem_post(&mutex2); // Release the mutex
        sem_post(&data2); // Notify that a slot is filled
      }
    }
    pthread_exit(NULL);
  }

int main() {
  clock_t start, end;
  double cpu_time;

  pthread_t t1_1, t1_2;
  // Create small and large random integer arrays
  for (int i = 0; i < SMALL; i++) {
    smallArr[i] = rand();
  }

  for (int i = 0; i < LARGE; i++) {
    largeArr[i] = rand();
  }

  printf("Small Global Max initialized: %d\n", globalMaxSmall[0]);
  printf("Small array: ");
  for (int i = 0; i < SMALL; i++) {
    printf("%d ", smallArr[i]);
  }
  sem_init(&mutex1, 0, 1);
  sem_init(&data1, 0, 0);
  start = clock();
  pthread_create(&t1_1, NULL, findMaxSmall, &smallArr);
  pthread_join(t1_1, NULL);
  end = clock();
  cpu_time = ((double)end-start) / CLOCKS_PER_SEC;
  sem_destroy(&mutex1);
  sem_destroy(&data1);
  printf("\nSmall Global Max after: %d", globalMaxSmall[0]);
  printf("\nExecution time with 1 worker thread: %f\n", cpu_time);

  printf("\nLarge Global Max initialized: %d\n", globalMaxLarge[0]);
  printf("Large array: ");
  for (int i = 0; i < LARGE; i++) {
    printf("%d ", largeArr[i]);
  }
  sem_init(&mutex2, 0, 1);
  sem_init(&data2, 0, 0);
  start = clock();
  pthread_create(&t1_2, NULL, findMaxLarge, &largeArr);
  pthread_join(t1_2, NULL);
  end = clock();
  cpu_time = ((double)end-start) / CLOCKS_PER_SEC;
  sem_destroy(&mutex2);
  sem_destroy(&data2);
  printf("\nLarge Global Max after: %d\n", globalMaxLarge[0]);
  printf("Execution time with 1 worker thread: %f", cpu_time);

  return 0;
}


Overwriting project1_s_1.c


In [10]:
%%shell
gcc project1_s_1.c -o project1_s_1
./project1_s_1

Small Global Max initialized: 0
Small array: 1804289383 846930886 1681692777 1714636915 1957747793 424238335 719885386 1649760492 596516649 1189641421 1025202362 1350490027 783368690 1102520059 2044897763 1967513926 1365180540 1540383426 304089172 1303455736 35005211 521595368 294702567 1726956429 336465782 861021530 278722862 233665123 2145174067 468703135 1101513929 1801979802 
Small Global Max after: 2145174067
Execution time with 1 worker thread: 0.000058

Large Global Max initialized: 0
Large array: 1315634022 635723058 1369133069 1125898167 1059961393 2089018456 628175011 1656478042 1131176229 1653377373 859484421 1914544919 608413784 756898537 1734575198 1973594324 149798315 2038664370 1129566413 184803526 412776091 1424268980 1911759956 749241873 137806862 42999170 982906996 135497281 511702305 2084420925 1937477084 1827336327 572660336 1159126505 805750846 1632621729 1100661313 1433925857 1141616124 84353895 939819582 2001100545 1998898814 1548233367 610515434 1585990364 13743

In [11]:
%%writefile project1_s_2.c
#include <stdio.h>
#include <stdlib.h>
#include <pthread.h>
#include <semaphore.h>
#include <unistd.h>
#include <time.h>

// 4 semaphores: 2 for small array max function and 2 for large array max function
// No empty semaphore as shared value does not need to be empty to be overwritten
sem_t mutex1, data1, mutex2, data2;
int globalMaxSmall[1] = {0};
int globalMaxLarge[1] = {0};

#define SMALL 32
#define LARGE 131072
int smallArr[SMALL];
int largeArr[LARGE];

// Find maximum in small array by iterating through entire array and comparing to global maximum
// Only write to max when current value is larger than global max
// Semaphores as buffer solution (CMPSC 472 Lecture 6)
void* findMaxSmall(void* arg) {
    for (int i = 0; i < SMALL; i++) {
      if (smallArr[i] > globalMaxSmall[0]) {
        sem_wait(&mutex1); // Get exclusive access to the buffer
        globalMaxSmall[0] = smallArr[i]; // Add item to the buffer
        sem_post(&mutex1); // Release the mutex
        sem_post(&data1); // Notify that a slot is filled
      }
    }
    pthread_exit(NULL);
  }

// Find maximum in large array by iterating through entire array and comparing to global maximum
// Only write to max when current value is larger than global max
// Semaphores as buffer solution (CMPSC 472 Lecture 6)
void* findMaxLarge(void* arg) {
    for (int i = 0; i < LARGE; i++) {
      if (largeArr[i] > globalMaxLarge[0]) {
        sem_wait(&mutex2); // Get exclusive access to the buffer
        globalMaxLarge[0] = largeArr[i]; // Add item to the buffer
        sem_post(&mutex2); // Release the mutex
        sem_post(&data2); // Notify that a slot is filled
      }
    }
    pthread_exit(NULL);
  }

int main() {
  clock_t start, end;
  double cpu_time;

  pthread_t t1_1, t2_1, t1_2, t2_2;
  // Create small and large random integer arrays
  for (int i = 0; i < SMALL; i++) {
    smallArr[i] = rand();
  }

  for (int i = 0; i < LARGE; i++) {
    largeArr[i] = rand();
  }

  printf("Small Global Max initialized: %d\n", globalMaxSmall[0]);
  printf("Small array: ");
  for (int i = 0; i < SMALL; i++) {
    printf("%d ", smallArr[i]);
  }
  sem_init(&mutex1, 0, 1);
  sem_init(&data1, 0, 0);
  start = clock();
  pthread_create(&t1_1, NULL, findMaxSmall, &smallArr);
  pthread_create(&t2_1, NULL, findMaxSmall, &smallArr);
  pthread_join(t1_1, NULL);
  pthread_join(t2_1, NULL);
  end = clock();
  cpu_time = ((double)end-start) / CLOCKS_PER_SEC;
  sem_destroy(&mutex1);
  sem_destroy(&data1);
  printf("\nSmall Global Max after: %d\n", globalMaxSmall[0]);
  printf("Execution time with 2 worker threads: %f\n", cpu_time);

  printf("\nLarge Global Max initialized: %d\n", globalMaxLarge[0]);
  printf("Large array: ");
  for (int i = 0; i < LARGE; i++) {
    printf("%d ", largeArr[i]);
  }
  sem_init(&mutex2, 0, 1);
  sem_init(&data2, 0, 0);
  start = clock();
  pthread_create(&t1_2, NULL, findMaxLarge, &largeArr);
  pthread_create(&t2_2, NULL, findMaxLarge, &largeArr);
  pthread_join(t1_2, NULL);
  pthread_join(t2_2, NULL);
  end = clock();
  cpu_time = ((double)end-start) / CLOCKS_PER_SEC;
  sem_destroy(&mutex2);
  sem_destroy(&data2);
  printf("\nLarge Global Max after: %d\n", globalMaxLarge[0]);
  printf("Execution time with 2 worker threads: %f", cpu_time);

  return 0;
}


Overwriting project1_s_2.c


In [12]:
%%shell
gcc project1_s_2.c -o project1_s_2
./project1_s_2

Small Global Max initialized: 0
Small array: 1804289383 846930886 1681692777 1714636915 1957747793 424238335 719885386 1649760492 596516649 1189641421 1025202362 1350490027 783368690 1102520059 2044897763 1967513926 1365180540 1540383426 304089172 1303455736 35005211 521595368 294702567 1726956429 336465782 861021530 278722862 233665123 2145174067 468703135 1101513929 1801979802 
Small Global Max after: 2145174067
Execution time with 2 worker threads: 0.000110

Large Global Max initialized: 0
Large array: 1315634022 635723058 1369133069 1125898167 1059961393 2089018456 628175011 1656478042 1131176229 1653377373 859484421 1914544919 608413784 756898537 1734575198 1973594324 149798315 2038664370 1129566413 184803526 412776091 1424268980 1911759956 749241873 137806862 42999170 982906996 135497281 511702305 2084420925 1937477084 1827336327 572660336 1159126505 805750846 1632621729 1100661313 1433925857 1141616124 84353895 939819582 2001100545 1998898814 1548233367 610515434 1585990364 1374

In [13]:
%%writefile project1_s_4.c
#include <stdio.h>
#include <stdlib.h>
#include <pthread.h>
#include <semaphore.h>
#include <unistd.h>
#include <time.h>

// 4 semaphores: 2 for small array max function and 2 for large array max function
// No empty semaphore as shared value does not need to be empty to be overwritten
sem_t mutex1, data1, mutex2, data2;
int globalMaxSmall[1] = {0};
int globalMaxLarge[1] = {0};

#define SMALL 32
#define LARGE 131072
int smallArr[SMALL];
int largeArr[LARGE];

// Find maximum in small array by iterating through entire array and comparing to global maximum
// Only write to max when current value is larger than global max
// Semaphores as buffer solution (CMPSC 472 Lecture 6)
void* findMaxSmall(void* arg) {
    for (int i = 0; i < SMALL; i++) {
      if (smallArr[i] > globalMaxSmall[0]) {
        sem_wait(&mutex1); // Get exclusive access to the buffer
        globalMaxSmall[0] = smallArr[i]; // Add item to the buffer
        sem_post(&mutex1); // Release the mutex
        sem_post(&data1); // Notify that a slot is filled
      }
    }
    pthread_exit(NULL);
  }

// Find maximum in large array by iterating through entire array and comparing to global maximum
// Only write to max when current value is larger than global max
// Semaphores as buffer solution (CMPSC 472 Lecture 6)
void* findMaxLarge(void* arg) {
    for (int i = 0; i < LARGE; i++) {
      if (largeArr[i] > globalMaxLarge[0]) {
        sem_wait(&mutex2); // Get exclusive access to the buffer
        globalMaxLarge[0] = largeArr[i]; // Add item to the buffer
        sem_post(&mutex2); // Release the mutex
        sem_post(&data2); // Notify that a slot is filled
      }
    }
    pthread_exit(NULL);
  }

int main() {
  clock_t start, end;
  double cpu_time;

  pthread_t t1_1, t2_1, t3_1, t4_1;
  pthread_t t1_2, t2_2, t3_2, t4_2;
  // Create small and large random integer arrays
  for (int i = 0; i < SMALL; i++) {
    smallArr[i] = rand();
  }

  for (int i = 0; i < LARGE; i++) {
    largeArr[i] = rand();
  }

  printf("Small Global Max initialized: %d\n", globalMaxSmall[0]);
  printf("Small array: ");
  for (int i = 0; i < SMALL; i++) {
    printf("%d ", smallArr[i]);
  }
  sem_init(&mutex1, 0, 1);
  sem_init(&data1, 0, 0);
  start = clock();
  pthread_create(&t1_1, NULL, findMaxSmall, &smallArr);
  pthread_create(&t2_1, NULL, findMaxSmall, &smallArr);
  pthread_create(&t3_1, NULL, findMaxSmall, &smallArr);
  pthread_create(&t4_1, NULL, findMaxSmall, &smallArr);
  pthread_join(t1_1, NULL);
  pthread_join(t2_1, NULL);
  pthread_join(t3_1, NULL);
  pthread_join(t4_1, NULL);
  end = clock();
  cpu_time = ((double)end-start) / CLOCKS_PER_SEC;
  sem_destroy(&mutex1);
  sem_destroy(&data1);
  printf("\nSmall Global Max after: %d\n", globalMaxSmall[0]);
  printf("Execution time with 4 worker threads: %f\n", cpu_time);

  printf("\nLarge Global Max initialized: %d\n", globalMaxLarge[0]);
  printf("Large array: ");
  for (int i = 0; i < LARGE; i++) {
    printf("%d ", largeArr[i]);
  }
  sem_init(&mutex2, 0, 1);
  sem_init(&data2, 0, 0);
  start = clock();
  pthread_create(&t1_2, NULL, findMaxLarge, &largeArr);
  pthread_create(&t2_2, NULL, findMaxLarge, &largeArr);
  pthread_create(&t3_2, NULL, findMaxLarge, &largeArr);
  pthread_create(&t4_2, NULL, findMaxLarge, &largeArr);
  pthread_join(t1_2, NULL);
  pthread_join(t2_2, NULL);
  pthread_join(t3_2, NULL);
  pthread_join(t4_2, NULL);
  end = clock();
  cpu_time = ((double)end-start) / CLOCKS_PER_SEC;
  sem_destroy(&mutex2);
  sem_destroy(&data2);
  printf("\nLarge Global Max after: %d\n", globalMaxLarge[0]);
  printf("Execution time with 4 worker threads: %f", cpu_time);

  return 0;
}


Overwriting project1_s_4.c


In [14]:
%%shell
gcc project1_s_4.c -o project1_s_4
./project1_s_4

Small Global Max initialized: 0
Small array: 1804289383 846930886 1681692777 1714636915 1957747793 424238335 719885386 1649760492 596516649 1189641421 1025202362 1350490027 783368690 1102520059 2044897763 1967513926 1365180540 1540383426 304089172 1303455736 35005211 521595368 294702567 1726956429 336465782 861021530 278722862 233665123 2145174067 468703135 1101513929 1801979802 
Small Global Max after: 2145174067
Execution time with 4 worker threads: 0.000159

Large Global Max initialized: 0
Large array: 1315634022 635723058 1369133069 1125898167 1059961393 2089018456 628175011 1656478042 1131176229 1653377373 859484421 1914544919 608413784 756898537 1734575198 1973594324 149798315 2038664370 1129566413 184803526 412776091 1424268980 1911759956 749241873 137806862 42999170 982906996 135497281 511702305 2084420925 1937477084 1827336327 572660336 1159126505 805750846 1632621729 1100661313 1433925857 1141616124 84353895 939819582 2001100545 1998898814 1548233367 610515434 1585990364 1374

In [15]:
%%writefile project1_s_8.c
#include <stdio.h>
#include <stdlib.h>
#include <pthread.h>
#include <semaphore.h>
#include <unistd.h>
#include <time.h>

// 4 semaphores: 2 for small array max function and 2 for large array max function
// No empty semaphore as shared value does not need to be empty to be overwritten
sem_t mutex1, data1, mutex2, data2;
int globalMaxSmall[1] = {0};
int globalMaxLarge[1] = {0};

#define SMALL 32
#define LARGE 131072
int smallArr[SMALL];
int largeArr[LARGE];

// Find maximum in small array by iterating through entire array and comparing to global maximum
// Only write to max when current value is larger than global max
// Semaphores as buffer solution (CMPSC 472 Lecture 6)
void* findMaxSmall(void* arg) {
    for (int i = 0; i < SMALL; i++) {
      if (smallArr[i] > globalMaxSmall[0]) {
        sem_wait(&mutex1); // Get exclusive access to the buffer
        globalMaxSmall[0] = smallArr[i]; // Add item to the buffer
        sem_post(&mutex1); // Release the mutex
        sem_post(&data1); // Notify that a slot is filled
      }
    }
    pthread_exit(NULL);
  }

// Find maximum in large array by iterating through entire array and comparing to global maximum
// Only write to max when current value is larger than global max
// Semaphores as buffer solution (CMPSC 472 Lecture 6)
void* findMaxLarge(void* arg) {
    for (int i = 0; i < LARGE; i++) {
      if (largeArr[i] > globalMaxLarge[0]) {
        sem_wait(&mutex2); // Get exclusive access to the buffer
        globalMaxLarge[0] = largeArr[i]; // Add item to the buffer
        sem_post(&mutex2); // Release the mutex
        sem_post(&data2); // Notify that a slot is filled
      }
    }
    pthread_exit(NULL);
  }

int main() {
  clock_t start, end;
  double cpu_time;

  pthread_t t1_1, t2_1, t3_1, t4_1, t5_1, t6_1, t7_1, t8_1;
  pthread_t t1_2, t2_2, t3_2, t4_2, t5_2, t6_2, t7_2, t8_2;
  // Create small and large random integer arrays
  for (int i = 0; i < SMALL; i++) {
    smallArr[i] = rand();
  }

  for (int i = 0; i < LARGE; i++) {
    largeArr[i] = rand();
  }

  printf("Small Global Max initialized: %d\n", globalMaxSmall[0]);
  printf("Small array: ");
  for (int i = 0; i < SMALL; i++) {
    printf("%d ", smallArr[i]);
  }
  sem_init(&mutex1, 0, 1);
  sem_init(&data1, 0, 0);
  start = clock();
  pthread_create(&t1_1, NULL, findMaxSmall, &smallArr);
  pthread_create(&t2_1, NULL, findMaxSmall, &smallArr);
  pthread_create(&t3_1, NULL, findMaxSmall, &smallArr);
  pthread_create(&t4_1, NULL, findMaxSmall, &smallArr);
  pthread_create(&t5_1, NULL, findMaxSmall, &smallArr);
  pthread_create(&t6_1, NULL, findMaxSmall, &smallArr);
  pthread_create(&t7_1, NULL, findMaxSmall, &smallArr);
  pthread_create(&t8_1, NULL, findMaxSmall, &smallArr);
  pthread_join(t1_1, NULL);
  pthread_join(t2_1, NULL);
  pthread_join(t3_1, NULL);
  pthread_join(t4_1, NULL);
  pthread_join(t5_1, NULL);
  pthread_join(t6_1, NULL);
  pthread_join(t7_1, NULL);
  pthread_join(t8_1, NULL);
  end = clock();
  cpu_time = ((double)end-start) / CLOCKS_PER_SEC;
  sem_destroy(&mutex1);
  sem_destroy(&data1);
  printf("\nSmall Global Max after: %d\n", globalMaxSmall[0]);
  printf("Execution time with 8 worker threads: %f\n", cpu_time);

  printf("\nLarge Global Max initialized: %d\n", globalMaxLarge[0]);
  printf("Large array: ");
  for (int i = 0; i < LARGE; i++) {
    printf("%d ", largeArr[i]);
  }
  sem_init(&mutex2, 0, 1);
  sem_init(&data2, 0, 0);
  start = clock();
  pthread_create(&t1_2, NULL, findMaxLarge, &largeArr);
  pthread_create(&t2_2, NULL, findMaxLarge, &largeArr);
  pthread_create(&t3_2, NULL, findMaxLarge, &largeArr);
  pthread_create(&t4_2, NULL, findMaxLarge, &largeArr);
  pthread_create(&t5_2, NULL, findMaxLarge, &largeArr);
  pthread_create(&t6_2, NULL, findMaxLarge, &largeArr);
  pthread_create(&t7_2, NULL, findMaxLarge, &largeArr);
  pthread_create(&t8_2, NULL, findMaxLarge, &largeArr);
  pthread_join(t1_2, NULL);
  pthread_join(t2_2, NULL);
  pthread_join(t3_2, NULL);
  pthread_join(t4_2, NULL);
  pthread_join(t5_2, NULL);
  pthread_join(t6_2, NULL);
  pthread_join(t7_2, NULL);
  pthread_join(t8_2, NULL);
  end = clock();
  cpu_time = ((double)end-start) / CLOCKS_PER_SEC;
  sem_destroy(&mutex2);
  sem_destroy(&data2);
  printf("\nLarge Global Max after: %d\n", globalMaxLarge[0]);
  printf("Execution time with 8 worker threads: %f", cpu_time);

  return 0;
}

Overwriting project1_s_8.c


In [16]:
%%shell
gcc project1_s_8.c -o project1_s_8
./project1_s_8

Small Global Max initialized: 0
Small array: 1804289383 846930886 1681692777 1714636915 1957747793 424238335 719885386 1649760492 596516649 1189641421 1025202362 1350490027 783368690 1102520059 2044897763 1967513926 1365180540 1540383426 304089172 1303455736 35005211 521595368 294702567 1726956429 336465782 861021530 278722862 233665123 2145174067 468703135 1101513929 1801979802 
Small Global Max after: 2145174067
Execution time with 8 worker threads: 0.000595

Large Global Max initialized: 0
Large array: 1315634022 635723058 1369133069 1125898167 1059961393 2089018456 628175011 1656478042 1131176229 1653377373 859484421 1914544919 608413784 756898537 1734575198 1973594324 149798315 2038664370 1129566413 184803526 412776091 1424268980 1911759956 749241873 137806862 42999170 982906996 135497281 511702305 2084420925 1937477084 1827336327 572660336 1159126505 805750846 1632621729 1100661313 1433925857 1141616124 84353895 939819582 2001100545 1998898814 1548233367 610515434 1585990364 1374